In [2]:
from pricing.structure import Structure
from utils import *

C:\Users\tales\Miniconda3\envs\TF_Newest\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


Using TensorFlow backend.


C:\Users\tales\Miniconda3\envs\TF_Newest\lib\site-packages\gensim\utils.py:862: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


C:\Users\tales\Miniconda3\envs\TF_Newest\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [4]:
tf.__version__,keras.__version__


('1.8.0', '2.1.6')

In [6]:
link = 'postgres://udmar9f385gb3o:p5c35862bd63c7c5070e64040171be67b0c6da0e18200d241c04e215329fd8cb3@ec2-18-234-15-254.compute-1.amazonaws.com:5432/dfcor1iq1tm3i7'
# link = 'sqlite:///C:\\Users\\tales\Code\crypto_data_scraper\\revised_scraper\\fundamental_database.db'
disk_engine = create_engine(link, echo=False)
fundamental = pd.read_sql('fundamental_data', disk_engine)
twitter = pd.read_sql('twitter_database', disk_engine)
chan = pd.read_sql('4chan_database', disk_engine)
full_train = pd.read_sql('Augmented_Train', disk_engine)
full_test = pd.read_sql('Augmented_Test', disk_engine)

try:
    reddit = pd.read_sql('reddit_database', disk_engine)
    print(full_train.shape, full_test.shape, fundamental.shape, twitter.shape, chan.shape, reddit.shape)

except Exception as e:
    print(e)
    print(full_train.shape, full_test.shape, fundamental.shape, twitter.shape, chan.shape)



(psycopg2.ProgrammingError) syntax error at or near "reddit_database"
LINE 1: reddit_database
        ^
 [SQL: 'reddit_database'] (Background on this error at: http://sqlalche.me/e/f405)
(38127, 203) (749, 203) (41400, 140) (6362, 15) (234407, 7)


In [33]:
span = 120
tar_periods = 7

sample_df = pd.read_sql('BTC_Train', con=disk_engine)

target_cat_cols = [f'{i+1}_per_tar_cat' for i in range(tar_periods)]

target_val_cols = [f'{i+1}_per_tar_val' for i in range(tar_periods)]

target_cols = target_cat_cols+target_val_cols

drop_cols = [
 'index',
 'id',

]



cat_cols = [
 'name',
 'symbol',
 'rank',
 'Event_Count',
 'Time',
 'max_sell_ex',
 'min_sell_ex',
 'max_buy_ex',
 'min_buy_ex',
 'Time_Year',
 'Time_Month',
 'Time_Week',
 'Time_Day',
 'Time_Dayofweek',
 'Time_Dayofyear',
 'Time_Hour',
 'Time_Minute',
 'Time_Is_month_end',
 'Time_Is_month_start',
 'Time_Is_quarter_end',
 'Time_Is_quarter_start',
 'Time_Is_year_end',
 'Time_Is_year_start',
 'Time_Elapsed'
]

# timeseries_cols = [[f"Minute_Price_{i}" for i in range(span)], [f"Minute_Volume_{i}" for i in range(span)],
#                    [f"Hourly_Price_{i}" for i in range(span)], [f"Hourly_Volume_{i}" for i in range(span)],
#                    [f"Daily_Price_{i}" for i in range(span)], [f"Daily_Volume_{i}" for i in range(span)]]
# 
# ts_cols = [j for i in timeseries_cols for j in i]

ts_cols = []

con_cols = [col for col in list(sample_df) if col not in target_cols+drop_cols+cat_cols+ts_cols]

cleaned = full_train[cat_cols+con_cols+target_cols+ts_cols]

KeyError: "['1_per_tar_val' '2_per_tar_val' '3_per_tar_val' '4_per_tar_val' '5_per_tar_val'\n '6_per_tar_val' '7_per_tar_val'] not in index"

In [8]:
for col in con_cols:
    full_train[col].fillna(full_train[col].median(), inplace=True)
    full_test[col].fillna(full_test[col].median(), inplace=True)

    
for col in cat_cols:
    full_train[col].fillna("None", inplace=True)
    full_test[col].fillna("None", inplace=True)


In [9]:
full_train.isnull().sum()

name                                0
symbol                              0
rank                                0
max_sell_ex                         0
min_sell_ex                         0
max_buy_ex                          0
min_buy_ex                          0
Event_Count                         0
Time                                0
Time_Year                           0
Time_Month                          0
Time_Week                           0
Time_Day                            0
Time_Dayofweek                      0
Time_Dayofyear                      0
Time_Hour                           0
Time_Minute                         0
Time_Is_month_end                   0
Time_Is_month_start                 0
Time_Is_quarter_end                 0
Time_Is_quarter_start               0
Time_Is_year_end                    0
Time_Is_year_start                  0
Time_Elapsed                        0
active_assets                       0
active_currencies                   0
active_marke

In [9]:
strk = Structure(cleaned, target_cols, cat_cols, con_cols, [])

In [17]:
strk.processing()

In [18]:
strk.load_emb_model('C:\\Users\\tales\Code\crypto_process\models\emb_model.h5')
strk.load_img_model('C:\\Users\\tales\Code\crypto_process\models\img_model.h5')
strk.load_nn_model('C:\\Users\\tales\Code\crypto_process\models\\nn_model.h5')

Loading emb_model...


Loaded emb_model!
Loading img_model...


Loaded img_model!
Loading img_model...


Loaded img_model!


In [19]:
strk.chart_train(2, 32, 0.0001, 0.1, layers=[256, 512, 1024], dropouts=[0.5, 0.4, 0.3], model=strk.img_model, shuffle=True, save=True)

Epoch 1/2


In [ ]:
strk.embedding_train(2, 32, 0.0001, 0.1, layers=[256, 512, 1024, 2048], dropouts=[0.5, 0.4, 0.3, 0.2], model=strk.emb_model, shuffle=True, save=True)

Epoch 1/25


  1/237 [..............................] - ETA: 4:52 - loss: 3.0268

  2/237 [..............................] - ETA: 2:56 - loss: 2.9643

  3/237 [..............................] - ETA: 2:18 - loss: 2.9469

  4/237 [..............................] - ETA: 1:59 - loss: 2.8469

...

210/237 [=========================>....] - ETA: 7s - loss: 2.6444

211/237 [=========================>....] - ETA: 7s - loss: 2.6435

212/237 [=========================>....] - ETA: 6s - loss: 2.6414

213/237 [=========================>....] - ETA: 6s - loss: 2.6414

KeyboardInterrupt: 

In [ ]:
strk.intermediate_outputs()

In [ ]:
strk.nn_train(2, 32, 0.0001, 0.1, layers=[256, 512, 1024], dropouts=[0.5, 0.4, 0.3], model=strk.nn_model, shuffle=True, save=True)

Epoch 1/3


  1/237 [..............................] - ETA: 11:08:29 - loss: 2.2403

  2/237 [..............................] - ETA: 5:48:34 - loss: 2.1695 

  3/237 [..............................] - ETA: 3:52:13 - loss: 2.3848

  4/237 [..............................] - ETA: 2:54:03 - loss: 2.3148

...

234/237 [============================>.] - ETA: 0s - loss: 2.6312

235/237 [============================>.] - ETA: 0s - loss: 2.6288

236/237 [============================>.] - ETA: 0s - loss: 2.6270

237/237 [==============================] - 70s 293ms/step - loss: 2.6280 - val_loss: 2.5754



Epoch 00003: loss did not improve


In [10]:
strk.load_intermediates(r"C:\Users\tales\Code\crypto_process\notebooks\img_emb_outs.csv")

In [12]:
strk.intermediate.shape

(20288, 10339)

In [10]:
from tensorflow.python import estimator

In [19]:
regressor = estimator.BoostedTreesRegressor(list(strk.intermediate), 100)

INFO:tensorflow:Using default config.


INFO:tensorflow:Using config: {'_model_dir': 'C:\\Users\\tales\\AppData\\Local\\Temp\\tmpqmrx8vbn', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000001DBC1B5C978>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


In [69]:
full_train.isnull().sum()

name                                   0
symbol                                 0
rank                                   0
max_sell_ex                         1747
min_sell_ex                         1747
max_buy_ex                          1747
min_buy_ex                          1747
Event_Count                            0
Time                                   0
Time_Year                              0
Time_Month                             0
Time_Week                              0
Time_Day                               0
Time_Dayofweek                         0
Time_Dayofyear                         0
Time_Hour                              0
Time_Minute                            0
Time_Is_month_end                      0
Time_Is_month_start                    0
Time_Is_quarter_end                    0
Time_Is_quarter_start                  0
Time_Is_year_end                       0
Time_Is_year_start                     0
Time_Elapsed                           0
active_assets   

In [34]:
class Estimator:
    def __init__(self, train_data, test_data, feature_columns, target_columns):
        self.train_data = {}
        for key in list(train_data[feature_columns]):
            vals = train_data[key].values
            self.train_data[key] = vals.astype(float)
        self.train_targets = train_data[target_columns].values.astype(float)
        print('Train data processed!')

        self.test_data = {}
        for key in list(test_data[feature_columns]):
            vals = test_data[key].values
            self.test_data[key] = vals.astype(float)
        self.test_targets = test_data[target_columns].values.astype(float)
        print('Test data processed!')

        
        self.bucketized_columns = []
        for col in feature_columns:
            data = train_data[col].astype(float)
            boundaries = sorted([data.min(), data.mean(), data.max()])
            numeric_col = tf.feature_column.numeric_column(col)
            try:
                bucketized_col = tf.feature_column.bucketized_column(numeric_col, boundaries=boundaries)
            except ValueError:
                bucketized_col = tf.feature_column.bucketized_column(numeric_col, boundaries=[-1.0, 0.0, 1.0])
            self.bucketized_columns.append(bucketized_col)
        self.feature_columns = feature_columns
        self.target_columns = target_columns

    def train_input_fn(self, feature_dict, label_array, batch_size):
        """An input function for training"""
        
        # Convert the inputs to a Dataset.
        dataset = tf.data.Dataset.from_tensor_slices((feature_dict, label_array))
    
        # Shuffle, repeat, and batch the examples.
        return dataset.shuffle(42).repeat().batch(batch_size)

    
    def boosted_tree(self, type, batch_size):
        if type == 'regressor':
            tree = estimator.BoostedTreesRegressor(self.bucketized_columns, 
                                                   n_batches_per_layer=int(len(self.train_data)/batch_size))
        elif type == 'classifier':
            n_classes = len(np.unique(self.test_targets))
            print(n_classes)
            tree = estimator.BoostedTreesClassifier(self.bucketized_columns, 
                                                    n_batches_per_layer=int(len(self.train_data)/batch_size), 
                                                    n_classes=len(np.unique(self.test_targets)))
        else:
            print('Error: Incorrect tree_type passed. Breaking')
            tree = "None"

        tree.train(input_fn=lambda:self.train_input_fn(self.train_data, self.train_targets, batch_size))
        
        return tree
    
    def dnn(self, type, batch_size):
        if type == 'regressor':

            reg = estimator.DNNLinearCombinedRegressor(dnn_feature_columns=self.bucketized_columns, 
                                                       dnn_activation_fn=tf.nn.elu, 
                                                       dnn_hidden_units=[100,100,100])
        elif type == 'classifier':
            reg = estimator.DNNLinearCombinedClassifier(dnn_feature_columns=self.bucketized_columns, 
                                                       dnn_activation_fn=tf.nn.elu, 
                                                       dnn_hidden_units=[100,100,100],
                                                        n_classes=len(np.unique(self.test_targets)))
        else:
            print('Error: Incorrect net_type passed. Breaking')
            reg = "None"
            
        reg.train(input_fn=lambda:self.train_input_fn(self.train_data, self.train_targets, batch_size))
        return reg


        

In [35]:
Est = Estimator(full_train, full_test, con_cols, ['7_per_tar_cat'])

Train data processed!
Test data processed!


In [27]:
for key in Est.train_data:
    print(key)
    print(Est.train_data[key])
    print(Est.train_data[key].dtype)
    print('-----------------------')

active_assets
[702. 702. 702. ... 699. 702. 702.]
float64
-----------------------
active_currencies
[897. 896. 896. ... 888. 896. 896.]
float64
-----------------------
active_markets
[10540. 10534. 10534. ... 10436. 10629. 10586.]
float64
-----------------------
bitcoin_percentage_of_market_cap
[38.04 37.99 38.01 ... 36.66 37.87 37.87]
float64
-----------------------
total_24h_volume_usd
[2.9161e+10 2.8946e+10 2.8301e+10 ... 3.2399e+10 2.7635e+10 2.7408e+10]
float64
-----------------------
total_market_cap_usd
[3.9563e+11 3.9631e+11 3.9403e+11 ... 4.3241e+11 3.9937e+11 3.9899e+11]
float64
-----------------------
price_usd
[ 0.3753  0.375   0.3709 ... 83.7371  0.4667  0.4697]
float64
-----------------------
price_btc
[0.     0.     0.     ... 0.009  0.0001 0.0001]
float64
-----------------------
24h_volume_usd
[1.5255e+08 1.5118e+08 1.4792e+08 ... 2.5488e+06 9.2005e+06 9.2731e+06]
float64
-----------------------
market_cap_usd
[6.9694e+09 6.9632e+09 6.8881e+09 ... 5.9836e+08 1.6335e+08 

In [36]:
regressor = Est.boosted_tree('regressor', 32)

INFO:tensorflow:Using default config.


INFO:tensorflow:Using config: {'_model_dir': 'C:\\Users\\tales\\AppData\\Local\\Temp\\tmpimj2a8ba', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000001B5EA0AF048>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


INFO:tensorflow:Calling model_fn.


INFO:tensorflow:Done calling model_fn.


INFO:tensorflow:Create CheckpointSaverHook.


...

INFO:tensorflow:global_step/sec: 29.6219


INFO:tensorflow:loss = 0.40958178, step = 2900 (3.389 sec)


INFO:tensorflow:Saving checkpoints for 3000 into C:\Users\tales\AppData\Local\Temp\tmpimj2a8ba\model.ckpt.


Type is unsupported, or the types of the items don't match field type in CollectionDef.
'_Resource' object has no attribute 'name'


INFO:tensorflow:Loss for final step: 0.33289358.


In [37]:
regressor = Est.dnn('regressor', 32)

INFO:tensorflow:Using default config.


INFO:tensorflow:Using config: {'_model_dir': 'C:\\Users\\tales\\AppData\\Local\\Temp\\tmpuwvynm1f', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000001B5DEA87D30>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


INFO:tensorflow:Calling model_fn.


INFO:tensorflow:Done calling model_fn.


INFO:tensorflow:Create CheckpointSaverHook.


...

INFO:tensorflow:loss = 7.263301, step = 2190900 (3.115 sec)


INFO:tensorflow:global_step/sec: 32.6305


INFO:tensorflow:loss = 12.803572, step = 2191000 (3.063 sec)


INFO:tensorflow:global_step/sec: 33.8128


INFO:tensorflow:loss = 25.025677, step = 2191100 (2.959 sec)
